# Day 15: [Warehouse Woes](https://adventofcode.com/2024/day/15)

## Pseudo code
1. Store map and robot movement sequence from the input 
    - Move sequence should be stored as one line of string
2. Starting from the location of the robot (@), move robots and change location of boxes (O) accordingly. Then update the map.
    - Walls (#) cannot be moved
3. Calculate the GPS coordinate
    - 100 * (1+y_axis) + 1* (1+x_axis)

## 1. Input to map and movement sequences

In [1]:
with open('day15-1.txt','r') as f:
    input_text = [lines.strip() for lines in f]
input_text

['##################################################',
 '#...#......O.........#O.....O#.....O.........O..##',
 '#.O.O#...O#O...O#...OO.#...O......OO#O.O...OO....#',
 '#...O..#O.....#.....O.....O..O.....OOO....O......#',
 '#.O..O.#O.O......OO..O.O....O...O...#.#........O.#',
 '#OO..#..O.O.....O...#.O....O.........#.OOO....OO.#',
 '#.OO.O........#.O....OO........OO.O...#O...O#..OO#',
 '##........O.O.O..#....#.......OOOO..O...O#..OO..O#',
 '#......O##.#O.OO.#...O.#.O.O....O.....OOO...#OO..#',
 '#.OOOO.OO..O.OOOO...OOO.......#.#...OO.OO....#.O##',
 '#........OO.#O.O.#.O..O..O.....O.#..O..O...OOO..##',
 '#...#.OO#.......#.O.OO..O....O.#.....O...O#.####.#',
 '#.....OO..O.#.O..O.O.##.O..#OO.O...O.O..OO#...#..#',
 '#O.OOOOO...OOO..#....O#.....O.....O.O.O...O...OO.#',
 '#...O.....OO.O.......O..#O....O......O.O.O...OO..#',
 '#.O...OO.O.O..O#........#..O##...#.O#..O.OO.#O.#.#',
 '#O.O.....#...OO.O....O..O.OO......O..OO.OO..#.O.##',
 '#..O......OO#.O..O.OO...O..O.O..O..........O..O..#',
 '#O..#...

In [2]:
import numpy as np

separator = input_text.index('')    # Separator between map and movement sequences

lmap = np.array(input_text[:separator])     # Store map
lmap = np.array([np.array([*l]) for l in lmap], dtype= object)
mseq = ''.join(input_text[separator+1:])   # Store movement sequences

print(f'Size of the map (including borderline #s)\nHeight: {len(lmap)}\nWidth: {len(lmap[0])}')
print(lmap)
print(mseq)

Size of the map (including borderline #s)
Height: 50
Width: 50
[['#' '#' '#' ... '#' '#' '#']
 ['#' '.' '.' ... '.' '#' '#']
 ['#' '.' 'O' ... '.' '.' '#']
 ...
 ['#' '.' '.' ... '.' 'O' '#']
 ['#' '.' '.' ... '.' '.' '#']
 ['#' '#' '#' ... '#' '#' '#']]
v<>v>^^vv<<v>v<v^>^vv<v>v>>^vv>>vv>^>^v^^v>>v>vv>^>><v^vv^<v>vv<>v^>>^>v>^<>vvvv<v^>>>v>^>v>^^<v>>v^><v>>vv^^^v<v><^>>v^^v^>^^<v^v<>^<<><<>>^><^v^<>^vv<v^><><>vv<>v^<^^<^<^<vv>vv^<<>><v>vv^^<^^^><>^^>^v>v^>^^v^^vv>^<<^v>v<vv<<^>^>>v>vv^v><>v^^><>^vv^<<<v^<><>^v<^v><^^vv^<>><<v<^^^^vv<v<>>>v<^^v<>^^>^>><v<v>v^<v>>>>><v>^<^><>v>^<v><v<^<^vv^<vv^vv>>vv><>^v<vvv^v^>v<v^^<<<^v><>vv^vv>v><vv>v>^<>vv<^v^v<>>>>><>v^>v<<>v<<^vv<vvvvv>>v>^<>>>>vv<<>^<^>><>v<^vv^>^>v^><>vvv<>>^<^<><>>vv>^^v^v>>>^><vv<><v^v<^^^<<^v>v>v<<<^v<>^<>^<v>v^v>><v>vv<>v>><v^v^><<^<>><<v^^>>^>^v^<>><^<<v<^vvv<><v^vvv<<><v<<vv^<^<^<>^<vvv^><^><<v>^v<><v<vv<>^^<^<>^^<><>^<^<<>>v<<><^vv^<<vv<^>^v<>v<v<^v>>>v^vv<^v>v<><^>><v>^>^<^>^><<><<vv><v^v^>^>^^>^>>>v^^>^^^<^>>>v<<>v>^<<

## 2. Move the robot

Based on the movement indicator, rotate the robot and identify the elements that are ahead. Locate the first wall (#) that the robot will run into. If there are box(es), push the box(es) to the first wall. Then update the map.


In [3]:
def move_boxes(direction):
    # Find closest # from @ and show the path just before #
    wall = min(list(*np.where(direction == '#')))
    path = [direction[:wall]][0]
    # Move one slot
    try:
        if path[1] == 'O':          # If there is a box right in front
            temp = 1                # To count consecutive Os from @
            p = 2
            while path[p] == 'O':
                temp += 1
                p += 1
            path[2:p+1] = 'O'

        path[0] = '.'
        path[1] = '@'
    except:
        print('error')
        pass


    # Update the path to direction
    direction[:wall] = path
    return direction

In [4]:
for m in mseq:
    r_y, r_x = list(zip(*np.where(lmap == '@')))[0] # Robot location

    if m == '^':        # Up
        direction = np.flip(lmap[:r_y+1,r_x])
        lmap[:r_y+1,r_x] = np.flip(move_boxes(direction))
    elif m == 'v':      # Down
        direction = lmap[r_y:,r_x]
        lmap[r_y:,r_x] = move_boxes(direction)
    elif m == '<':      # Left
        direction = np.flip(lmap[r_y,:r_x+1])
        lmap[r_y,:r_x+1] = np.flip(move_boxes(direction))
    elif m == '>':      # Right
        direction = lmap[r_y,r_x:]
        lmap[r_y,r_x:] = move_boxes(direction)
    print(m)
    print(lmap)
    print('\n')

v
[['#' '#' '#' ... '#' '#' '#']
 ['#' '.' '.' ... '.' '#' '#']
 ['#' '.' 'O' ... '.' '.' '#']
 ...
 ['#' '.' '.' ... '.' 'O' '#']
 ['#' '.' '.' ... '.' '.' '#']
 ['#' '#' '#' ... '#' '#' '#']]


<
[['#' '#' '#' ... '#' '#' '#']
 ['#' '.' '.' ... '.' '#' '#']
 ['#' '.' 'O' ... '.' '.' '#']
 ...
 ['#' '.' '.' ... '.' 'O' '#']
 ['#' '.' '.' ... '.' '.' '#']
 ['#' '#' '#' ... '#' '#' '#']]


>
[['#' '#' '#' ... '#' '#' '#']
 ['#' '.' '.' ... '.' '#' '#']
 ['#' '.' 'O' ... '.' '.' '#']
 ...
 ['#' '.' '.' ... '.' 'O' '#']
 ['#' '.' '.' ... '.' '.' '#']
 ['#' '#' '#' ... '#' '#' '#']]


v
[['#' '#' '#' ... '#' '#' '#']
 ['#' '.' '.' ... '.' '#' '#']
 ['#' '.' 'O' ... '.' '.' '#']
 ...
 ['#' '.' '.' ... '.' 'O' '#']
 ['#' '.' '.' ... '.' '.' '#']
 ['#' '#' '#' ... '#' '#' '#']]


error
>
[['#' '#' '#' ... '#' '#' '#']
 ['#' '.' '.' ... '.' '#' '#']
 ['#' '.' 'O' ... '.' '.' '#']
 ...
 ['#' '.' '.' ... '.' 'O' '#']
 ['#' '.' '.' ... '.' '.' '#']
 ['#' '#' '#' ... '#' '#' '#']]


^
[['#' '#' '#

## 3. Calculate the GPS coordinate
  Formula : 100 * (1+y_axis) + 1 * (1+x_axis)

In [5]:
coordinates = list(zip(*np.where(lmap == 'O')))
coordinates

[(1, 8),
 (1, 12),
 (1, 13),
 (1, 18),
 (1, 22),
 (1, 23),
 (1, 24),
 (1, 26),
 (1, 27),
 (1, 28),
 (1, 30),
 (1, 31),
 (1, 32),
 (1, 33),
 (1, 34),
 (1, 35),
 (1, 45),
 (1, 46),
 (1, 47),
 (2, 2),
 (2, 4),
 (2, 6),
 (2, 8),
 (2, 21),
 (2, 22),
 (2, 25),
 (2, 34),
 (2, 35),
 (2, 48),
 (3, 4),
 (3, 8),
 (3, 15),
 (3, 16),
 (3, 18),
 (3, 21),
 (3, 22),
 (3, 31),
 (3, 37),
 (3, 39),
 (3, 40),
 (4, 2),
 (4, 12),
 (4, 14),
 (4, 22),
 (4, 35),
 (4, 37),
 (5, 1),
 (5, 2),
 (5, 6),
 (5, 7),
 (5, 36),
 (5, 38),
 (5, 42),
 (5, 47),
 (5, 48),
 (6, 1),
 (6, 2),
 (6, 4),
 (6, 5),
 (6, 16),
 (6, 23),
 (6, 26),
 (6, 36),
 (6, 37),
 (6, 46),
 (6, 47),
 (6, 48),
 (7, 2),
 (7, 3),
 (7, 14),
 (7, 15),
 (7, 16),
 (7, 25),
 (7, 26),
 (7, 37),
 (7, 38),
 (7, 46),
 (7, 47),
 (7, 48),
 (8, 2),
 (8, 3),
 (8, 12),
 (8, 14),
 (8, 15),
 (8, 18),
 (8, 22),
 (8, 26),
 (8, 28),
 (8, 32),
 (8, 33),
 (8, 34),
 (8, 38),
 (8, 39),
 (8, 45),
 (8, 46),
 (8, 47),
 (9, 1),
 (9, 2),
 (9, 3),
 (9, 7),
 (9, 8),
 (9, 12),
 (9, 

In [6]:
gps = 0
for c in coordinates:
    gps += 100*c[0] + c[1]
print(f'Total GPS coordinates : {gps}')

Total GPS coordinates : 1406392
